In [29]:
class Flipflop:
    def __init__(self, destinations, name) -> None:
        self.destinations = destinations
        self.name = name
        self.stored = 0
        self.period = -1
        pass
    
    def add_period(self, cycle):
        if self.period == -1:
            self.period = cycle * 2

    def send_pulse(self, input, source, queue, cycle):
        if not input:
            self.stored = (self.stored + 1) % 2
            self.add_period(cycle)
            for destination in self.destinations:
                queue.append((destination, self.stored, self.name))
        return None

In [30]:
class Broadcaster:
    def __init__(self, destinations) -> None:
        self.destinations = destinations
        pass

In [31]:
class Conjunction:
    def __init__(self, destinations, name) -> None:
        self.destinations = destinations
        self.sources = []
        self.period = -1
        self.name = name
        self.memory = {}
        pass

    def add_source(self, source):
        self.sources.append(source)
        self.memory[source] = 0

    def add_period(self, cycle):
        if self.period == -1:
            self.period = cycle
    
    def send_pulse(self, input, source, queue, cycle):
        self.memory[source] = input
        if all([x == 1 for x in self.memory.values()]):
            self.add_period(cycle)
            value = 0
        else:
            value = 1
        for destination in self.destinations:
            queue.append((destination, value, self.name))

In [32]:
text = open("input.txt").read().split("\n")
text = [x.split(" -> ") for x in text]

modules = {}

for module in text:
    if module[0] == 'broadcaster':
        broadcaster = Broadcaster(module[1].split(", "))
    elif module[0][0] == '%':
        modules[module[0][1:]] = Flipflop(module[1].split(", "), module[0][1:])
    elif module[0][0] == '&':
        modules[module[0][1:]] = Conjunction(module[1].split(", "), module[0][1:])

for module in modules:
    flipflop = modules[module]
    for destination in flipflop.destinations:
        if destination in modules and isinstance(modules[destination], Conjunction):
            modules[destination].add_source(module)

modules['rx'] = Flipflop([], "rx")

In [33]:
count = 0
limit = 10000
queue = []
low_count = 0
high_count = 0
logs = []
while(True):
    if len(queue) == 0:
        logs.append({x.name: x.memory.copy() for x in modules.values() if isinstance(x, Conjunction)})
        if count >= limit:
            break
        count += 1
        low_count += 1
        for destination in broadcaster.destinations:
            low_count += 1
            modules[destination].send_pulse(0, 'broadcaster', queue, count)
    else:
        next_module, pulse, source = queue.pop(0)
        if next_module == 'rx' and pulse == 0:
            print(pulse, source, count)
        if pulse:
            high_count += 1
        else:
            low_count += 1
        modules[next_module].send_pulse(pulse, source, queue, count)
print(logs)

[{'bc': {'zh': 0, 'hk': 0, 'st': 0, 'nf': 0, 'mn': 0, 'dx': 0, 'tg': 0}, 'gj': {'sf': 0, 'nd': 0, 'sc': 0, 'qc': 0, 'xr': 0, 'pz': 0, 'cl': 0, 'tr': 0, 'sz': 0, 'jf': 0}, 'jm': {'sg': 0, 'lm': 0, 'dh': 0, 'db': 0}, 'sg': {'gj': 0}, 'lm': {'qq': 0}, 'qq': {'gv': 0, 'pl': 0, 'lz': 0, 'rh': 0, 'xf': 0, 'hn': 0, 'qj': 0}, 'bx': {'zx': 0, 'dg': 0, 'nq': 0, 'ms': 0, 'xh': 0, 'fr': 0, 'lr': 0, 'vt': 0, 'tb': 0, 'xc': 0, 'pm': 0}, 'dh': {'bc': 0}, 'db': {'bx': 0}}, {'bc': {'zh': 0, 'hk': 0, 'st': 0, 'nf': 0, 'mn': 1, 'dx': 0, 'tg': 0}, 'gj': {'sf': 0, 'nd': 0, 'sc': 0, 'qc': 0, 'xr': 1, 'pz': 0, 'cl': 0, 'tr': 0, 'sz': 0, 'jf': 0}, 'jm': {'sg': 0, 'lm': 0, 'dh': 0, 'db': 0}, 'sg': {'gj': 1}, 'lm': {'qq': 1}, 'qq': {'gv': 0, 'pl': 1, 'lz': 0, 'rh': 0, 'xf': 0, 'hn': 0, 'qj': 0}, 'bx': {'zx': 0, 'dg': 0, 'nq': 0, 'ms': 0, 'xh': 0, 'fr': 0, 'lr': 0, 'vt': 0, 'tb': 0, 'xc': 1, 'pm': 0}, 'dh': {'bc': 1}, 'db': {'bx': 1}}, {'bc': {'zh': 0, 'hk': 0, 'st': 0, 'nf': 0, 'mn': 0, 'dx': 0, 'tg': 0}, 'gj':

In [34]:
print(broadcaster.destinations, "Broadcaster")
for module in modules:
    if isinstance(modules[module], Conjunction):
        print([modules[x].period for x in modules[module].sources], modules[module].sources, modules[module].period, modules[module].name)

['pl', 'xr', 'mn', 'xc'] Broadcaster
[32, 4096, 64, 512, 2, 2048, 1024] ['zh', 'hk', 'st', 'nf', 'mn', 'dx', 'tg'] 3889 bc
[2048, 16, 4, 1024, 2, 4096, 256, 32, 64, 512] ['sf', 'nd', 'sc', 'qc', 'xr', 'pz', 'cl', 'tr', 'sz', 'jf'] 4027 gj
[1, 1, 1, 1] ['sg', 'lm', 'dh', 'db'] -1 jm
[4027] ['gj'] 1 sg
[3851] ['qq'] 1 lm
[1024, 2, 16, 4, 2048, 512, 4096] ['gv', 'pl', 'lz', 'rh', 'xf', 'hn', 'qj'] 3851 qq
[64, 16, 8, 128, 256, 2048, 1024, 512, 4096, 2, 4] ['zx', 'dg', 'nq', 'ms', 'xh', 'fr', 'lr', 'vt', 'tb', 'xc', 'pm'] 4079 bx
[3889] ['bc'] 1 dh
[4079] ['bx'] 1 db


In [36]:
import math
print(math.lcm(4027, 3851, 3889, 4079))

246006621493687
